In [1]:
import pandas as pd
from clustergrammer2 import Network, CGM2, net
df = {}

>> clustergrammer2 backend version 0.14.0


In [2]:
# df['ini'] = pd.read_csv('https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-states.csv')
df['ini'] = pd.read_csv('https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-counties.csv')
df['ini'].shape

(273314, 6)

In [3]:
list_fips = df['ini']['fips'].value_counts().index.tolist()
list_fips = [int(x) for x in list_fips]

In [4]:
pd.DataFrame(list_fips).to_csv('fips.txt')

In [5]:
df['ini'].head()

date     county       state     fips  cases  deaths
0  2020-01-21  Snohomish  Washington  53061.0      1       0
1  2020-01-22  Snohomish  Washington  53061.0      1       0
2  2020-01-23  Snohomish  Washington  53061.0      1       0
3  2020-01-24       Cook    Illinois  17031.0      1       0
4  2020-01-24  Snohomish  Washington  53061.0      1       0

In [6]:
df['mat'] = pd.DataFrame()
for inst_row in df['ini'].index.tolist():
    inst_date = df['ini'].loc[inst_row, 'date']
    inst_county = df['ini'].loc[inst_row, 'county']
    inst_cases = df['ini'].loc[inst_row, 'cases']
    
    df['mat'].loc[inst_county, inst_date] = inst_cases

# enforce date ordering    
dates = df['mat'].columns.tolist()
sorted(dates)
df['mat'] = df['mat'][dates]

# fill in missing value
net.load_df(df['mat'])
net.swap_nan_for_zero()
df['mat'] = net.export_df()

# calculate new cases in rolling 7 day window
list_ser = []
for inst_county in df['mat'].index.tolist():
    ser_county = df['mat'].loc[inst_county]
    ser_roll = ser_county.diff().rolling(7).mean()
#     ser_roll = ser_county.diff()
    list_ser.append(ser_roll)
    
df['diff'] = pd.concat(list_ser, axis=1).transpose()

# enforce date ordering
dates = df['diff'].columns.tolist()
sorted(dates)
df['diff'] = df['diff'][dates]

# get rid of nans
net.load_df(df['diff'])
net.swap_nan_for_zero()
df['diff'] = net.export_df()

# drop dates with no change
ser_date = df['diff'].sum(axis=0)
keep_dates = ser_date[ser_date > 0].index.tolist()
df['diff'] = df['diff'][keep_dates]

In [7]:
df['meta_county'] = pd.DataFrame()
for inst_row in df['ini'].index.tolist():
    inst_county = df['ini'].loc[inst_row, 'county']
    inst_state = df['ini'].loc[inst_row, 'state']    
    df['meta_county'].loc[inst_county, 'state'] = inst_state
df['meta_county'].shape

(1805, 1)

In [8]:
df['mat'].shape

(1805, 158)

In [9]:
# net.load_df(df['mat'])
# net.normalize(axis='row', norm_type='zscore')
# net.widget()

In [10]:
df['diff'].min(axis=1).sort_values()

Cook           -12035.428571
Middlesex        -593.285714
Camden           -425.857143
Hall             -204.714286
Duval             -98.571429
Unknown           -93.142857
Beaver            -87.142857
Orleans           -80.285714
Platte            -72.000000
Blaine            -70.857143
Terrell           -31.285714
Howard            -30.428571
Thomas            -29.000000
Shelby            -27.714286
Hardeman          -26.571429
Hampshire         -21.571429
Albany            -20.428571
Kane              -20.000000
St. Clair         -19.714286
Sussex            -18.142857
Lake              -17.571429
Knox              -16.857143
Morris            -16.857143
Caddo             -16.142857
Steele            -14.142857
Johnston          -13.428571
Decatur           -12.714286
Daviess           -12.571429
Evangeline        -12.571429
Hamilton          -11.571429
                    ...     
Marathon            0.000000
Green               0.000000
Dunn                0.000000
Kanawha       

In [11]:
df['diff-norm'] = net.umi_norm(df['diff'].transpose()).transpose()

In [12]:
# df['meta_county']

In [13]:
df['diff'].head()

2020-01-28  2020-01-29  2020-01-30  2020-01-31  2020-02-01  \
Snohomish      0.000000    0.000000    0.000000    0.000000    0.000000   
Cook           0.142857    0.142857    0.285714    0.142857    0.142857   
Orange         0.142857    0.142857    0.142857    0.142857    0.000000   
Maricopa       0.142857    0.142857    0.142857    0.142857    0.142857   
Los Angeles    0.142857    0.142857    0.142857    0.142857    0.142857   

             2020-02-02  2020-02-03  2020-02-04  2020-02-05  2020-02-06  \
Snohomish      0.000000    0.000000    0.000000    0.000000         0.0   
Cook           0.142857    0.142857    0.142857    0.142857         0.0   
Orange         0.000000    0.000000    0.000000    0.000000         0.0   
Maricopa       0.000000    0.000000    0.000000    0.000000         0.0   
Los Angeles    0.000000    0.000000    0.000000    0.000000         0.0   

                ...         2020-06-17    2020-06-18    2020-06-19  \
Snohomish       ...          15.571429     16.428571     16.000000   
Cook            ...      -11940.571429 -11996.714286 -12035.428571   
Orange          ...           2.285714      2.428571      1.714286   
Maricopa        ...         998.571429   1106.000000   1282.285714   
Los Angeles     ...        1446.428571   1336.000000   1304.714286   

              2020-06-20   2020-06-21   2020-06-22   2020-06-23   2020-06-24  \
Snohomish      16.000000    16.000000    21.714286    28.428571    27.428571   
Cook            0.000000     0.000000     0.000000     0.000000     0.000000   
Orange          1.857143     1.000000     1.000000     1.142857     0.857143   
Maricopa     1501.714286  1634.857143  1754.000000  1872.571429  1817.285714   
Los Angeles  1373.285714  1482.714286  1735.857143  1882.571429  1757.285714   

              2020-06-25   2020-06-26  
Snohomish      29.428571    30.714286  
Cook            0.000000     0.000000  
Orange          0.857143     1.000000  
Maricopa     1892.142857  1946.714286  
Los Angeles  1891.428571  1946.142857  

[5 rows x 151 columns]

In [14]:
df['diff-proc'] = df['diff'][keep_dates]

In [15]:
net = Network(CGM2)
net.load_df(df['diff-proc'], meta_row=df['meta_county'])
net.normalize(axis='row', norm_type='zscore', z_clip=5)
net.swap_nan_for_zero()
net.widget()

CGM2(network='{"row_nodes": [{"name": "Snohomish", "ini": 1805, "clust": 27, "rank": 705, "rankvar": 1137, "ca…

In [16]:
# dates = df['mat'].columns.tolist()
# sorted(dates)

In [17]:
from bqplot import *
from ipywidgets import Layout

import pandas as pd
# county_data = pd.read_csv('us-counties.csv')
county_data = pd.read_csv('https://raw.githubusercontent.com/nytimes/covid-19-data/master/us-counties.csv')
county_data = county_data[county_data['fips'].notna()]
county_data['fips'] = county_data['fips'].astype(int)
county_data['date'] = pd.to_datetime(county_data['date'])

total_county_data = county_data.groupby('fips')['deaths'].sum()
total_county_data.index = total_county_data.index.astype(int)

sc_geo_county = AlbersUSA()
sc_c1_county = ColorScale()

color_data_county = dict(zip(total_county_data.index, list(total_county_data)))

map_styles_county = {'color': color_data_county,
              'scales': {'projection': sc_geo_county, 'color': sc_c1_county}, 'colors': {'default_color': 'Grey'}}

axis_county = ColorAxis(scale=sc_c1_county)

county_map = Map(map_data=topo_load('map_data/USCountiesMap.json'), **map_styles_county)
county_fig = Figure(marks=[county_map], axes=[axis_county],title='US Elections 2008 - Example',
                    layout=Layout(min_width='800px', min_height='550px'))



In [18]:
total_county_data.head()

fips
1001    332
1003    512
1005     59
1007     50
1009     41
Name: deaths, dtype: int64

In [19]:
date_sc = DateScale()
count_sc_y = LinearScale(max=np.float(county_data.deaths.max()))

date_ax = Axis(scale=date_sc, label='Date')
count_ax = Axis(scale=count_sc_y, orientation='vertical', label='Deaths')

date_count = Lines(scales={'x': date_sc, 'y': count_sc_y})

bar_fig = Figure(marks=[date_count], axes=[date_ax, count_ax],
                 layout=Layout(min_width='600px', min_height='400px'))

def tooltip_function(name, value):
    state = value['data']['id']
    count_choice = county_data[county_data['fips'] == state]
    state_name = count_choice['state'].iloc[0]
    county_name = count_choice['county'].iloc[0]
    date_count.x = count_choice['date']
    date_count.y = count_choice['deaths']
    bar_fig.title = f'{county_name} {state_name}'

In [20]:
county_fig

Figure(axes=[ColorAxis(scale=ColorScale())], fig_margin={'top': 60, 'bottom': 60, 'left': 60, 'right': 60}, la…